# **NYU Wagner - Python Coding for Public Policy**
# Class 3: Data visualization

# Up front

## Resubmission

_Should_ be working now…? Has anyone been able to resubmit?

## ipytest

Helpful? Confusing?

## Participation

[The criteria](https://github.com/afeld/nyu-python-public-policy/blob/master/syllabus.md#participation) are changing.

# LECTURE

## **Today's goal**: Visualizing requests per community district to help us better understand trends across the city

## **Today's goal**: Visualizing requests per community district to help us better understand trends across the city

## Start by importing necessary packages

In [1]:
import pandas as pd
import plotly.express as px

# boilerplate for allowing PDF export
import plotly.io as pio
pio.renderers.default = "notebook_connected+pdf"

## Data from where we left off last class

Derived dataset containing count of complaints per community district.

In [2]:
districts = pd.read_csv('https://storage.googleapis.com/python-public-policy/data/311_community_districts.csv.zip')
districts.head()

borocd    Borough                       CD Name  2010 Population  \
0     112  Manhattan    Washington Heights, Inwood           190020   
1     405     Queens  Ridgewood, Glendale, Maspeth           169190   
2     412     Queens   Jamaica, St. Albans, Hollis           225919   
3     301   Brooklyn      Williamsburg, Greenpoint           173083   
4     303   Brooklyn            Bedford Stuyvesant           152985   

   count_of_311_requests  request_per_capita  
0                  81403            0.428392  
1                  71506            0.422637  
2                  70362            0.311448  
3                  68104            0.393476  
4                  66360            0.433768

## Let's start with making a histogram to better visualize the difference in scale of 311 requests across community boards

Adapting [the basic histogram example](https://plotly.com/python/histograms/):

In [3]:
fig = px.histogram(districts, x='count_of_311_requests')
fig.show()

As we said before, looking at raw volume is probably less useful than density.

1. [Open Homework 3](https://padmgp-4506-spring.rcnyu.org/user-redirect/notebooks/class_materials/hw_3.ipynb)
1. Complete `In-class exercise 1`

How does it compare to the chart of the raw counts?

In [4]:
fig = px.histogram(districts, x='request_per_capita')
fig.show()

In [5]:
fig = px.histogram(districts, x='count_of_311_requests')
fig.show()

Let's [improve the formatting](https://plotly.com/python/figure-labels/) (based on [the `.histogram()` documentation](https://plotly.com/python-api-reference/generated/plotly.express.histogram.html)):

In [6]:
fig = px.histogram(districts,
                   x='request_per_capita',
                   title='Volume of 311 requests, 2018-2019',
                   labels={'request_per_capita': '311 requests per capita'})

# y-axis needs to be done separately, since it's derived
fig.update_layout(yaxis_title_text='Number of community districts')
fig.show()

## Creating a stacked bar chart

In [7]:
fig = px.bar(districts,
             x='Borough',
             y='count_of_311_requests',
             hover_data=['borocd', 'CD Name'])

fig.show()

## Make a scatterplot of count of 311 requests per CD against CD population

In [8]:
fig = px.scatter(districts,
                 x='2010 Population',
                 y='count_of_311_requests',
                 hover_data=['borocd', 'CD Name'])

fig.show()

**Exercise 2:** [Add a trendline](https://plotly.com/python/linear-fits/).

In [9]:
fig = px.scatter(districts,
                 x='2010 Population',
                 y='count_of_311_requests',
                 hover_data=['borocd', 'CD Name'],
                 trendline='ols')

fig.show()

Let's take a look at the statistical summary, via the [`statsmodels`](https://www.statsmodels.org/) package, following [Plotly's example](https://plotly.com/python/linear-fits/#fitting-multiple-lines-and-retrieving-the-model-parameters):

In [10]:
trend_results = px.get_trendline_results(fig).iloc[0,0]
trend_results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.471
Model:                            OLS   Adj. R-squared:                  0.462
Method:                 Least Squares   F-statistic:                     50.73
Date:                Thu, 14 Apr 2022   Prob (F-statistic):           1.99e-09
Time:                        20:52:26   Log-Likelihood:                -626.67
No. Observations:                  59   AIC:                             1257.
Df Residuals:                      57   BIC:                             1261.
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const       1.528e+04   4424.730      3.453      0.001    6416.292    2.41e+04
x1             0.2173      0.031      7.122      0.000       0.156       0.278
==============================================================================
Omnibus:                        0.008   Durbin-Watson:                   1.996
Prob(Omnibus):                  0.996   Jarque-Bera (JB):                0.065
Skew:                           0.006   Prob(JB):                        0.968
Kurtosis:                       2.837   Cond. No.                     4.88e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 4.88e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

["In general, the higher the R-squared, the better the model fits your data."](https://blog.minitab.com/blog/adventures-in-statistics-2/regression-analysis-how-do-i-interpret-r-squared-and-assess-the-goodness-of-fit)

## Let's try styling the scatter plot with different colors for each borough

In [11]:
fig = px.scatter(districts,
                 x='2010 Population',
                 y='count_of_311_requests',
                 color='Borough')
fig.show()

## Bonus: Produce a map of complaint counts by CD

Following [this example](https://plotly.com/python/choropleth-maps/#indexing-by-geojson-properties), using [community district GIS data](https://data.cityofnewyork.us/City-Government/Community-Districts/yfnk-k7r4):

In [12]:
# inspect the GeoJSON data; we'll just use the URL and the property name

import requests

geojson_url = 'https://data.cityofnewyork.us/api/geospatial/yfnk-k7r4?method=export&format=GeoJSON'

response = requests.get(geojson_url)
geojson_data = response.json()
geojson_data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'boro_cd': '206',
    'shape_area': '42664311.5086',
    'shape_leng': '35875.7117328'},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[-73.8718461029101, 40.843760777855834],
       [-73.87191691517283, 40.84345374264658],
       [-73.87196432156817, 40.84323825377388],
       [-73.87213357846727, 40.842497794549],
       [-73.87231748546176, 40.84169028202043],
       [-73.87234056327031, 40.841583626189504],
       [-73.87236365249346, 40.841476960983385],
       [-73.87239558060885, 40.84133637543188],
       [-73.872527839146, 40.840753983006856],
       [-73.87267805874693, 40.840137197106756],
       [-73.87277204658531, 40.83975128233606],
       [-73.87298042939128, 40.83895248518574],
       [-73.87312728158687, 40.83833509641596],
       [-73.87314714674842, 40.83826389897314],
       [-73.87317603928548, 40.838165830892954],
       [-73.87332746697363, 40.83765194933224],
     

In [13]:
fig = px.choropleth_mapbox(districts,
                           geojson=geojson_url,
                           locations='borocd',
                           featureidkey='properties.boro_cd',
                           color='request_per_capita',
                           hover_data=['CD Name'],
                           center = {'lat': 40.73, 'lon': -73.98},
                           zoom=9,
                           mapbox_style='carto-positron')

fig.update_layout(height=700)
fig.show()

Midtown, as an outlier, is skewing our results. Let's exclude it.

In [14]:
no_midtown = districts[districts.borocd != 105]

fig = px.choropleth_mapbox(no_midtown,
                           geojson=geojson_url,
                           locations='borocd',
                           featureidkey='properties.boro_cd',
                           color='request_per_capita',
                           hover_data=['CD Name'],
                           center = {'lat': 40.73, 'lon': -73.98},
                           zoom=9,
                           mapbox_style='carto-positron')

fig.update_layout(height=700)
fig.show()

**Tip:** Make sure your `locations` match your `featureidkey`.

**Fun fact** (for a certain kind of person): [What the Mapbox zoom level means](https://docs.mapbox.com/help/glossary/zoom-level/)

## Chart hygiene

- Always include a title
- Make sure you label dependent and independent variables (X and Y axes)
- Consider whether you are working with continuous vs. discrete values

## Pivoting

Pandas supports [reshaping](https://pandas.pydata.org/pandas-docs/stable/user_guide/reshaping.html) DataFrames through [pivoting](https://pandas.pydata.org/pandas-docs/stable/user_guide/reshaping.html#reshaping-by-pivoting-dataframe-objects), [like spreadsheets do](https://support.google.com/docs/answer/1272900).

In [15]:
%%html
<video controls width="700">
  <source src="https://github.com/afeld/python-public-policy/raw/main/extras/img/pivot.mp4" type="video/mp4">
</video>

# HOMEWORK 3

Please refer to the [HW3 Starter Notebook](https://padmgp-4506-spring.rcnyu.org/user-redirect/notebooks/class_materials/hw_3.ipynb).